In [1]:
import pandas as pd
import numpy as np
import pandas as pd
import numpy as np
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.manifold import TSNE
import plotly.express as px
import hdbscan
from sklearn.cluster import KMeans
import re
import stopwordsiso as stopwords
import spacy

In [2]:
#!python -m spacy download pl_core_news_sm

In [3]:
file_path = 'data//text_all.jsonl'  
data = pd.read_json(file_path, lines=True)


labels_map = {
    0: "pozytywny wydźwięk",
    1: "neutralny wydźwięk",
    2: "negatywny wydźwięk",
    3: "mowa nienawiści",
    '0': "pozytywny wydźwięk",
    '1': "neutralny wydźwięk",
    '2': "negatywny wydźwięk",
    '3': "mowa nienawiści"
}

data["label"] = data["label"].replace(labels_map)
data.head()


text               label
0  @USER Nic, nic,nic nieważne, jutro albo w najb...  neutralny wydźwięk
1  @USER Kibic @USER odpowiada @USER i @USER na k...  neutralny wydźwięk
2              Mówi że stare rapsy są całkiem niezle  neutralny wydźwięk
3  @USER @USER Zaległości były, ale ważne czy był...  neutralny wydźwięk
4           @USER @USER Oby nie spierdolil na północ  negatywny wydźwięk

In [4]:
unique_labels = data['label'].explode().unique()
print(unique_labels)

['neutralny wydźwięk' 'negatywny wydźwięk' 'pozytywny wydźwięk'
 'mowa nienawiści']


In [5]:
data = data[data['label'].apply(lambda x: len(x) > 0)] 
data['label'] = data['label'].apply(lambda x: x[0] if isinstance(x, list) and len(x) > 0 else x)

In [6]:
nlp = spacy.load("pl_core_news_sm")

polish_stopwords = stopwords.stopwords("pl")

def preprocess_text(text):
    text = re.sub(r'@\w+', '', text)

    text = re.sub(r'[^\w\s]', '', text)
    text = re.sub(r'\d+', '', text)
    text = text.strip()

    doc = nlp(text)

    lemmatized_words = [token.lemma_ for token in doc if token.lemma_.lower() not in polish_stopwords]

    return ' '.join(lemmatized_words)

data['cleaned_text'] = data['text'].apply(preprocess_text)


In [7]:
data.head()

text               label  \
0  @USER Nic, nic,nic nieważne, jutro albo w najb...  neutralny wydźwięk   
1  @USER Kibic @USER odpowiada @USER i @USER na k...  neutralny wydźwięk   
2              Mówi że stare rapsy są całkiem niezle  neutralny wydźwięk   
3  @USER @USER Zaległości były, ale ważne czy był...  neutralny wydźwięk   
4           @USER @USER Oby nie spierdolil na północ  negatywny wydźwięk   

                                        cleaned_text  
0    nicnic nieważny jutro bliski czas odezwąć narka  
1  kibic   odpowiadać     krytyka Manuel Junconnh...  
2                   mówić stary rapsy całkiem niezle  
3     Zaległość ważny wezwanie zapłata klub wywiązać  
4                              Oby spierdolil północ

# TfidfVectorizer

In [8]:
vectorizer = TfidfVectorizer()
tfidf_embeddings = vectorizer.fit_transform(data['cleaned_text']).toarray()

In [9]:
tsne = TSNE(n_components=2, random_state=42)
tsne_results = tsne.fit_transform(tfidf_embeddings)

tsne_df = pd.DataFrame(tsne_results, columns=['x', 'y'])
tsne_df['label'] = data['label']
tsne_df['text'] = data['text']

fig = px.scatter(tsne_df, x='x', y='y', color='label', 
                 title='Wizualizacja osadzeń TF-IDF przy użyciu t-SNE',
                 labels={'label': 'Wydźwięk'},
                 hover_name=tsne_df['text'], 
                 color_discrete_sequence=px.colors.qualitative.Vivid)

fig.update_traces(marker=dict(size=10),
                  selector=dict(mode='markers'))

fig.show()

In [10]:
vectorizer = TfidfVectorizer()
tfidf_embeddings = vectorizer.fit_transform(data['cleaned_text']).toarray()

hdbscan_model_tfidf = hdbscan.HDBSCAN(min_cluster_size=2)
labels_tfidf = hdbscan_model_tfidf.fit_predict(tfidf_embeddings)

data['cluster_tfidf'] = labels_tfidf

tsne_tfidf = TSNE(n_components=2, random_state=42)
tsne_results_tfidf = tsne_tfidf.fit_transform(tfidf_embeddings)

tsne_df_tfidf = pd.DataFrame(tsne_results_tfidf, columns=['x', 'y'])
tsne_df_tfidf['cluster'] = data['cluster_tfidf']
tsne_df_tfidf['text'] = data['text']

fig_tfidf = px.scatter(tsne_df_tfidf, x='x', y='y', color='cluster',
                       title='Wizualizacja klastrów z HDBSCAN dla TF-IDF',
                       labels={'cluster': 'Klaster'},
                       hover_name=tsne_df_tfidf['text'],
                       color_discrete_sequence=px.colors.qualitative.Vivid)

fig_tfidf.show()


In [11]:
tfidf_embeddings = np.array(tfidf_embeddings)

n_clusters = 4

kmeans = KMeans(n_clusters=n_clusters, random_state=42)
kmeans.fit(tfidf_embeddings)

data['kmeans_cluster'] = kmeans.labels_


In [12]:
tsne = TSNE(n_components=2, random_state=42)
X_tsne = tsne.fit_transform(tfidf_embeddings)

tsne_df = pd.DataFrame(X_tsne, columns=['x', 'y'])
tsne_df['kmeans_cluster'] = data['kmeans_cluster']
tsne_df['text'] = data['text']

fig = px.scatter(tsne_df, x='x', y='y', color='kmeans_cluster',
                 title='Wizualizacja klastrów z K-means dla TF-IDF',
                 labels={'kmeans_cluster': 'Klastry'}, 
                 hover_name=tsne_df['text'],
                 color_discrete_sequence=px.colors.qualitative.Vivid)

fig.show()


# Universal Sentence Encoder

In [13]:
import tensorflow_hub as hub

model_url = "https://tfhub.dev/google/universal-sentence-encoder/4"
model = hub.load(model_url)

def get_use_embeddings(texts, model):
    return model(texts).numpy()

use_embeddings = get_use_embeddings(data['cleaned_text'].tolist(), model)

In [14]:
tsne = TSNE(n_components=2, random_state=42, perplexity=30)
tsne_results = tsne.fit_transform(use_embeddings)

In [15]:
tsne_df = pd.DataFrame(tsne_results, columns=['x', 'y'])
tsne_df['label'] = data['label']
tsne_df['text'] = data['text']

fig = px.scatter(tsne_df, x='x', y='y', color='label',
                 title='Wizualizacja t-SNE osadzeń Universal Sentence Encoder',
                 labels={'label': 'Wydźwięk'},
                 hover_name=tsne_df['text'],
                 color_discrete_sequence=px.colors.qualitative.Pastel)

fig.show()

In [16]:
hdbscan_model_use = hdbscan.HDBSCAN(min_cluster_size=20)
labels_use = hdbscan_model_use.fit_predict(use_embeddings)

data['cluster_use'] = labels_use

tsne_use = TSNE(n_components=2, random_state=42)
tsne_results_use = tsne_use.fit_transform(use_embeddings)

tsne_df_use = pd.DataFrame(tsne_results_use, columns=['x', 'y'])
tsne_df_use['cluster'] = data['cluster_use']
tsne_df_use['text'] = data['text']

fig_use = px.scatter(tsne_df_use, x='x', y='y', color='cluster',
                     title='Wizualizacja klastrów z HDSCAN dla USE',
                     labels={'cluster': 'Klaster'},
                     hover_name=tsne_df_use['text'],
                     color_discrete_sequence=px.colors.qualitative.Pastel)

fig_use.show()

In [17]:
use_embeddings = np.array(use_embeddings)
n_clusters = 4

kmeans = KMeans(n_clusters=n_clusters, random_state=42)
kmeans.fit(use_embeddings)

data['kmeans_cluster'] = kmeans.labels_


In [18]:
tsne = TSNE(n_components=2, random_state=42)
X_tsne = tsne.fit_transform(use_embeddings)

tsne_df = pd.DataFrame(X_tsne, columns=['x', 'y'])
tsne_df['kmeans_cluster'] = data['kmeans_cluster']
tsne_df['text'] = data['text']

fig = px.scatter(tsne_df, x='x', y='y', color='kmeans_cluster',
                 title='Wizualizacja klastrów z K-means dla USE',
                 labels={'kmeans_cluster': 'Klastry'},
                 hover_name=tsne_df['text'],
                 color_discrete_sequence=px.colors.qualitative.Pastel)

fig.show()
